In [168]:
import plyvel
from itertools import islice

%run -i read_tree.py

In [ ]:
db = plyvel.DB('../node/nodedir/data/application.db')
height = max_height(db)
height

In [ ]:
it = iterate(db, 's/k:mint/', height)
[k for k, v in it]
it.inner.lookups

In [ ]:
dict(parse_struct(next(iterate(db, 's/k:mint/', height, key = [138]))[1]))

In [ ]:
it = iterate(db, 's/k:emissions/', height, key = [62, 64], format = 'Qss')
ooiiregrets = [(k[2],k[3],value[1],float(value[2])) for k,v in it for value in (dict(parse_struct(v)),)]

len(ooiiregrets), it.inner.lookups

In [181]:
keynames = {0: "Params", 1: "TotalStake", 2: "TopicStake", 3: "Rewards", 4: "NextTopicId", 5: "Topics", 6: "TopicWorkers", 7: "TopicReputers", 8: "DelegatorStake", 9: "DelegateStakePlacement", 10: "TargetStake", 11: "Inferences", 12: "Forecasts", 13: "WorkerNodes", 14: "ReputerNodes", 15: "LatestInferencesTs", 16: "ActiveTopics", 17: "AllInferences", 18: "AllForecasts", 19: "AllLossBundles", 20: "StakeRemoval", 21: "StakeByReputerAndTopicId", 22: "DelegateStakeRemoval", 23: "AllTopicStakeSum", 24: "AddressTopics", 24: "WhitelistAdmins", 25: "ChurnableTopics", 26: "RewardableTopics", 27: "NetworkLossBundles", 28: "NetworkRegrets", 29: "StakeByReputerAndTopicId", 30: "ReputerScores", 31: "InferenceScores", 32: "ForecastScores", 33: "ReputerListeningCoefficient", 34: "InfererNetworkRegrets", 35: "ForecasterNetworkRegrets", 36: "OneInForecasterNetworkRegrets", 37: "OneInForecasterSelfNetworkRegrets", 38: "UnfulfilledWorkerNonces", 39: "UnfulfilledReputerNonces", 40: "FeeRevenueEpoch", 41: "TopicFeeRevenue", 42: "PreviousTopicWeight", 43: "PreviousReputerRewardFraction", 44: "PreviousInferenceRewardFraction", 45: "PreviousForecastRewardFraction", 46: "InfererScoreEmas", 47: "ForecasterScoreEmas", 48: "ReputerScoreEmas", 49: "TopicRewardNonce", 50: "DelegateRewardPerShare", 51: "PreviousPercentageRewardToStakedReputers", 52: "StakeRemovalsByBlock", 53: "DelegateStakeRemovalsByBlock", 54: "StakeRemovalsByActor", 55: "DelegateStakeRemovalsByActor", 56: "TopicLastWorkerCommit", 57: "TopicLastReputerCommit", 58: "TopicLastWorkerPayload", 59: "TopicLastReputerPayload", 60: "OpenWorkerWindows", 61: "LatestNaiveInfererNetworkRegrets", 62: "LatestOneOutInfererInfererNetworkRegrets", 63: "LatestOneOutInfererForecasterNetworkRegrets", 64: "LatestOneOutForecasterInfererNetworkRegrets", 65: "LatestOneOutForecasterForecasterNetworkRegrets", 66: "PreviousForecasterScoreRatio", 67: "LastDripBlock", 68: "TopicToNextPossibleChurningBlock", 69: "BlockToActiveTopics", 70: "BlockToLowestActiveTopicWeight", 71: "PreviousTopicQuantileInfererScoreEma", 72: "PreviousTopicQuantileForecasterScoreEma", 73: "PreviousTopicQuantileReputerScoreEma", 74: "CountInfererInclusionsInTopic", 75: "CountForecasterInclusionsInTopic", 76: "ActiveInferers", 77: "ActiveForecasters", 78: "ActiveReputers", 79: "LowestInfererScoreEma", 80: "LowestForecasterScoreEma", 81: "LowestReputerScoreEma", 82: "LossBundles", 83: "TotalSumPreviousTopicWeights", 84: "RewardCurrentBlockEmission", 85: "GlobalWhitelist", 86: "TopicCreatorWhitelist", 87: "TopicWorkerWhitelist", 88: "TopicReputerWhitelist", 89: "TopicWorkerWhitelistEnabled", 90: "TopicReputerWhitelistEnabled", 91: "LastMedianInferences", 92: "MadInferences", 93: "InitialInfererEmaScore", 94: "InitialForecasterEmaScore", 95: "InitialReputerEmaScore", 96: "GlobalWorkerWhitelist", 97: "GlobalReputerWhitelist", 98: "GlobalAdminWhitelist", 99: "LatestRegretStdNorm", 100: "LatestInfererWeights", 101: "LatestForecasterWeights", 102: "NetworkInferences", 103: "OutlierResistantNetworkInferences", 104: "MonthlyReputerRewards", 105: "MonthlyTopicRewards",}

In [ ]:
lens = np.zeros(256, dtype = int)

for field in range(255):
    lens[field] = count(db, 's/k:emissions/', height, key = [field])

order = np.lexsort((np.arange(256)[::-1], lens))[::-1]

print('Map lengths:')

for i in range(len(order)):
    if lens[order[i]] == 0 and order[i] not in keynames:
        break

    print(f'{keynames[order[i]]:50} {lens[order[i]]:9d}')

In [ ]:
# def has_prefix(db, prefix: bytes) -> bool:
#     it = db.iterator(start = prefix)
#     try:
#         first_key, _ = next(it)
#         return first_key.startswith(prefix)
#     except StopIteration:
#         return False
#     finally:
#         it.close()

# found = []
# prefixes = [b's/']

# for i in range(20):
#     new_prefixes = []

#     for p in prefixes:
#         for i in range(256):
#             b = p + bytes([i])
#             if has_prefix(db, b):
#                 if b.endswith(b'/'):
#                     found.append((b, db.approximate_size(b, b + b'\xff')))
#                 else:
#                     new_prefixes.append(b)
#                 # new_prefixes.append(b)

#     prefixes = new_prefixes

# found